In [1]:
!pip install pymupdf pandas openpyxl spacy classy-classification

     ---------------------------------------- 0.0/3.5 MB ? eta -:--:--
     ---------------------------------------- 0.0/3.5 MB ? eta -:--:--
     ---------------------------------------- 0.0/3.5 MB ? eta -:--:--
      --------------------------------------- 0.1/3.5 MB 469.7 kB/s eta 0:00:08
     - -------------------------------------- 0.1/3.5 MB 722.1 kB/s eta 0:00:05
     -- ------------------------------------- 0.2/3.5 MB 958.4 kB/s eta 0:00:04
     -- ------------------------------------- 0.3/3.5 MB 1.1 MB/s eta 0:00:03
     -- ------------------------------------- 0.3/3.5 MB 1.1 MB/s eta 0:00:03
     ---- ----------------------------------- 0.4/3.5 MB 1.2 MB/s eta 0:00:03
     ----- ---------------------------------- 0.5/3.5 MB 1.3 MB/s eta 0:00:03
     -------- ------------------------------- 0.8/3.5 MB 1.7 MB/s eta 0:00:02
     --------- ------------------------------ 0.9/3.5 MB 1.8 MB/s eta 0:00:02
     ------------ --------------------------- 1.1/3.5 MB 2.0 MB/s eta 0:00:02
 

  DEPRECATION: sentence-transformers is being installed using the legacy 'setup.py install' method, because it does not have a 'pyproject.toml' and the 'wheel' package is not installed. pip 23.1 will enforce this behaviour change. A possible replacement is to enable the '--use-pep517' option. Discussion can be found at https://github.com/pypa/pip/issues/8559

[notice] A new release of pip is available: 23.0.1 -> 23.2.1
[notice] To update, run: python.exe -m pip install --upgrade pip


     ----------------------------------- ---- 39.2/44.1 MB 1.3 MB/s eta 0:00:04
     ----------------------------------- ---- 39.3/44.1 MB 1.2 MB/s eta 0:00:04
     ----------------------------------- ---- 39.4/44.1 MB 1.2 MB/s eta 0:00:04
     ----------------------------------- ---- 39.4/44.1 MB 1.2 MB/s eta 0:00:04
     ----------------------------------- ---- 39.5/44.1 MB 1.3 MB/s eta 0:00:04
     ----------------------------------- ---- 39.6/44.1 MB 1.3 MB/s eta 0:00:04
     ------------------------------------ --- 39.8/44.1 MB 1.3 MB/s eta 0:00:04
     ------------------------------------ --- 39.8/44.1 MB 1.3 MB/s eta 0:00:04
     ------------------------------------ --- 39.8/44.1 MB 1.3 MB/s eta 0:00:04
     ------------------------------------ --- 39.8/44.1 MB 1.3 MB/s eta 0:00:04
     ------------------------------------ --- 39.8/44.1 MB 1.3 MB/s eta 0:00:04
     ------------------------------------ --- 39.9/44.1 MB 1.3 MB/s eta 0:00:04
     -----------------------------------

In [2]:
!python -m spacy download es_dep_news_trf

     ---------------------------------------- 0.0/407.8 MB ? eta -:--:--
     ---------------------------------------- 0.0/407.8 MB 1.9 MB/s eta 0:03:33
     ---------------------------------------- 0.0/407.8 MB 1.9 MB/s eta 0:03:33
     ---------------------------------------- 0.0/407.8 MB 1.9 MB/s eta 0:03:33
     ---------------------------------------- 0.0/407.8 MB 1.9 MB/s eta 0:03:33
     -------------------------------------- 0.1/407.8 MB 218.8 kB/s eta 0:31:04
     -------------------------------------- 0.1/407.8 MB 218.8 kB/s eta 0:31:04
     -------------------------------------- 0.1/407.8 MB 218.8 kB/s eta 0:31:04
     -------------------------------------- 0.1/407.8 MB 178.6 kB/s eta 0:38:03
     -------------------------------------- 0.1/407.8 MB 178.6 kB/s eta 0:38:03
     -------------------------------------- 0.1/407.8 MB 266.9 kB/s eta 0:25:28
     -------------------------------------- 0.1/407.8 MB 283.8 kB/s eta 0:23:57
     -------------------------------------- 0.1


[notice] A new release of pip is available: 23.0.1 -> 23.2.1
[notice] To update, run: python.exe -m pip install --upgrade pip


# Resumen Ejecutivo
Durante el proceso de revisión de los informes de práctica del DISC (Departamento de Ingeniería de Sistemas y Computación), se requiere una inversión considerable de tiempo que, hasta la fecha, no ha sido automatizada. Esto conlleva largas jornadas de trabajo y carga adicional para los académicos, quienes podrían emplear ese tiempo en otras labores. Por lo tanto, como equipo de trabajo, hemos llegado a un consenso en la necesidad de llevar a cabo el análisis y desarrollo de un modelo que permita clasificar los informes en las categorías definidas en la rúbrica actual (insatisfactorio, regular, bueno y excelente).
Es importante destacar que, con la llegada de la pandemia, la entrega de informes ha sido en formato digital, lo que ha generado un conjunto de aproximadamente 100 informes disponibles. Esta digitalización ofrece ventajas significativas para el entrenamiento del modelo, ya que se dispone de datos de entrada y resultados concretos (informe, rúbrica y nota).


In [1]:
import fitz
import pandas as pd
pd.set_option("mode.copy_on_write", True)

# Lectura de datos


In [2]:
def get_classification(grade, number=False):
  classification = [0,0,0] # Regular, Bueno, Excelente (Todo 0 = Insatisfactorio)
  grade = round(grade, 1)
  if(grade < 4):
    return "reprobado" if not number else 0
  elif (4 <= grade):
    classification[0] = 1
    return "aprobado" if not number else 1

In [3]:
dataset = pd.read_excel("calificaciones.xlsx", decimal=',')
grades_columns = dataset.columns.difference(["id", "periodo", "Unnamed: 9"]) #["estructura", "escritura", "contenido", "conclusiones", "conocimiento", "relevancia", "total"]
dataset = dataset.dropna(subset=grades_columns)

# Extracción y limpieza de documentos
En esta sección, se cargan los documentos en formato PDF, para la extracción y limpieza de estos, seguido de su integración al dataset.

In [5]:
documents = []

for id in dataset['id']:
    pdf_file = fitz.open(f"dataset/{id}.pdf")
    pdf_file.delete_page(0)
    document_text = chr(12).join([page.get_text() for page in pdf_file])
    documents.append(document_text)

dataset.insert(loc=2, column="documents", value=documents)
dataset

id periodo                                          documents  \
0    20908397-1  2023-1  ii \n \nÍndice General \n        Página     \n...   
1    18971994-1  2023-1   \n \nii \n \nÍndice General                  ...   
2    19445943-1  2023-1   \n2 \n \nÍndice general \n \nÍndice de figura...   
5    19463712-1  2023-1  ii \n \nÍNDICE GENERAL \nÍNDICE DE TABLAS .......   
6    20218430-1  2023-1  ii \n \nÍndice General \nÍndice de figuras ......   
..          ...     ...                                                ...   
148  20415620-1  2022-1   \n \nii \n \nÍNDICE \n \nNOMENCLATURA ..........   
149  20504070-1  2022-1   \n \nii \n \nÍndice general \nÍndice general ...   
150  20636426-1  2022-1   \n \n \nii \n \nÍndice General \n \n \n \n \n...   
151  20730369-1  2022-1  ii \n \n \nINDICE \n \n \nINDICE DE FIGURAS .....   
152  23078645-1  2022-1   \n \nii \n \nÍndice general \nÍndice de tabla...   

     estructura  escritura  contenido  conclusiones  conocimiento  relevancia  \
0           6.2        5.1        6.0           5.5           4.4         6.0   
1           6.9        6.8        6.8           6.8           7.0         6.9   
2           6.7        6.9        6.5           6.4           6.8         7.0   
5           4.4        4.9        4.9           5.8           4.0         6.0   
6           6.1        5.8        5.5           5.0           4.5         5.8   
..          ...        ...        ...           ...           ...         ...   
148         7.0        6.3        6.8           6.5           7.0         6.8   
149         4.0        6.8        4.8           6.5           6.5         6.3   
150         6.5        5.5        5.8           6.0           6.5         7.0   
151         6.8        4.0        5.8           5.7           5.0         6.5   
152         6.3        6.0        6.0           6.0           5.8         6.3   

     total Unnamed: 9  
0      5.3        NaN  
1      6.9        NaN  
2      6.7        NaN  
5      4.9        NaN  
6      5.2        NaN  
..     ...        ...  
148    6.8        NaN  
149    6.0        NaN  
150    6.2        NaN  
151    5.4        NaN  
152    6.0        NaN  

[146 rows x 11 columns]

# Preprocesamiento de etiquetas
Con base en las notas obtenidas por cada entrada, se clasifican los documentos en las categorías definidas en la rúbrica.
Se consideran dos tipos de etiquetas: texto y número. El primero se utiliza para el entrenamiento de modelos de Deep Learning, mientras que el segundo se utiliza para el entrenamiento de modelos tradicionales.

In [6]:
text_labeled_dataset = dataset.copy()
text_labeled_dataset.loc[:, grades_columns] = text_labeled_dataset.loc[:, grades_columns].apply(lambda s: s.apply(get_classification))
dataset.loc[:, grades_columns] = dataset.loc[:, grades_columns].apply(lambda s: s.apply(lambda x: get_classification(grade=x, number=True)))
dataset

C:\Users\jose6\AppData\Local\Temp\ipykernel_19120\1845537149.py:3: DeprecationWarning: In a future version, `df.iloc[:, i] = newvals` will attempt to set the values inplace instead of always setting a new array. To retain the old behavior, use either `df[df.columns[i]] = newvals` or, if columns are non-unique, `df.isetitem(i, newvals)`
  dataset.loc[:, grades_columns] = dataset.loc[:, grades_columns].apply(lambda s: s.apply(lambda x: get_classification(grade=x, number=True)))


id periodo                                          documents  \
0    20908397-1  2023-1  ii \n \nÍndice General \n        Página     \n...   
1    18971994-1  2023-1   \n \nii \n \nÍndice General                  ...   
2    19445943-1  2023-1   \n2 \n \nÍndice general \n \nÍndice de figura...   
5    19463712-1  2023-1  ii \n \nÍNDICE GENERAL \nÍNDICE DE TABLAS .......   
6    20218430-1  2023-1  ii \n \nÍndice General \nÍndice de figuras ......   
..          ...     ...                                                ...   
148  20415620-1  2022-1   \n \nii \n \nÍNDICE \n \nNOMENCLATURA ..........   
149  20504070-1  2022-1   \n \nii \n \nÍndice general \nÍndice general ...   
150  20636426-1  2022-1   \n \n \nii \n \nÍndice General \n \n \n \n \n...   
151  20730369-1  2022-1  ii \n \n \nINDICE \n \n \nINDICE DE FIGURAS .....   
152  23078645-1  2022-1   \n \nii \n \nÍndice general \nÍndice de tabla...   

     estructura  escritura  contenido  conclusiones  conocimiento  relevancia  \
0             1          1          1             1             1           1   
1             1          1          1             1             1           1   
2             1          1          1             1             1           1   
5             1          1          1             1             1           1   
6             1          1          1             1             1           1   
..          ...        ...        ...           ...           ...         ...   
148           1          1          1             1             1           1   
149           1          1          1             1             1           1   
150           1          1          1             1             1           1   
151           1          1          1             1             1           1   
152           1          1          1             1             1           1   

     total Unnamed: 9  
0        1        NaN  
1        1        NaN  
2        1        NaN  
5        1        NaN  
6        1        NaN  
..     ...        ...  
148      1        NaN  
149      1        NaN  
150      1        NaN  
151      1        NaN  
152      1        NaN  

[146 rows x 11 columns]

# Clasificación de documentos con métodos tradicionales
Se usará SciKit-Learn para el análisis de los documentos mediante métodos tradicionales de NLP, como TF-IDF ~~y Word2Vec?~~. Se utilizará un modelo de clasificación de regresión logística y SVM para la clasificación de los documentos.
En primera instancia, solo se probará la clasificiación final.

In [7]:
from sklearn.feature_extraction.text import TfidfVectorizer 
from sklearn.svm import SVC
from sklearn.linear_model import RidgeClassifier, LogisticRegression
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score

In [8]:
Xn = dataset['documents']
yn = dataset['total']
X_train, X_test, y_train, y_test = train_test_split(Xn, yn, random_state=3, test_size=0.3)

In [9]:
vectorizer = TfidfVectorizer(ngram_range=(1, 3), max_df=0.9, min_df=0.2)
X_train_bow = vectorizer.fit_transform(X_train)
X_test_bow = vectorizer.transform(X_test)

In [10]:
svc_n = SVC(C=10)
svc_n.fit(X_train_bow, y_train)
y_pred = svc_n.predict(X_test_bow)
print(accuracy_score(y_test, y_pred))

0.9772727272727273


In [11]:
ridge = RidgeClassifier()
ridge.fit(X_train_bow, y_train)
y_pred_r = ridge.predict(X_test_bow)
print(accuracy_score(y_test, y_pred_r))

0.9772727272727273


In [12]:
log = LogisticRegression()
log.fit(X_train_bow, y_train)
y_pred_l = log.predict(X_test_bow)
print(accuracy_score(y_test, y_pred_l))

0.9772727272727273


# Clasificación de documentos con Deep Learning

In [13]:
Xn_text_labeled = text_labeled_dataset['documents']
yn_text_labeled = text_labeled_dataset['total']
X_text_train, X_text_test, y_text_train, y_text_test = train_test_split(Xn_text_labeled, yn_text_labeled, random_state=3, test_size=0.3)

In [14]:
training_data_total = {
  "reprobado": [],
  "aprobado": [],
}
for index, document in X_text_train.items():
  training_data_total[y_text_train[index]].append(document)
training_data_total

{'reprobado': ["ii \n \nÍndice General \nÍndice de figuras ............................................................................................................................................ iii \nNomenclatura ................................................................................................................................................ iv \nGlosario .......................................................................................................................................................... v \nResumen ........................................................................................................................................................ vi \nI. \nINTRODUCCIÓN.................................................................................................................................. i \n1. \nPresentación de la Organización ........................................................................................................ i \

https://spacy.io/universe/project/classyclassification

In [ ]:
from classy_classification import ClassyClassifier
classifier = ClassyClassifier(data=training_data_total)
classifier.set_embedding_model(model="paraphrase-multilingual-mpnet-base-v2")
y_text_pred = classifier.pipe(X_text_test.tolist())

In [ ]:
y_text_pred

In [ ]:
y_text_test